# Urban Mobility Trends Unveiled: A Comprehensive Analysis of Lyft Bikes in San Francisco
#### Machine Learning Pipeline Execution
Meta Team Members: Divya Dodla (ua03330), Naren Kandregula (pw71937), Sachin Dudam (gg42052)
##### Note: The machine learning portion is placed in a separate notebook due to automatic cluster dispatching, which incurs a higher load than usual. 
##### Please refer to the dedicated machine learning notebook for detailed insights into model training and evaluation.

In [0]:
from pyspark.sql import SparkSession
from pyspark.sql import functions as F
from pyspark.sql.functions import col, mean, count, unix_timestamp, dayofweek, year, month, dayofmonth, to_date, date_format, hour, avg, concat_ws, udf, lit, when, monotonically_increasing_id, coalesce, expr
from pyspark.sql.window import Window
from pyspark.sql.types import DoubleType, StringType, IntegerType, StructType, StructField, BinaryType

import pandas as pd
import numpy as np
import math

import matplotlib.pyplot as plt
import seaborn as sns

from pyspark.ml.feature import StringIndexer, VectorAssembler, StandardScaler
from pyspark.ml import Pipeline
from pyspark.ml.classification import LogisticRegression, RandomForestClassifier, MultilayerPerceptronClassifier
from pyspark.ml.evaluation import BinaryClassificationEvaluator, MulticlassClassificationEvaluator

In [0]:
# Create a Spark session
spark = SparkSession.builder.appName("ML_Lyft").getOrCreate()

In [0]:
# The 'new_ml_df' DataFrame is the final preprocessed dataset obtained from the "lyft_Baywheels" notebook. 
# It has undergone effective preprocessing steps and is now ready for use in machine learning tasks.

# Load data from CSV file into a DataFrame
new_ml_df = spark.read.csv("dbfs:/FileStore/tables/new_ml_df.csv", header=True, inferSchema=True)

In [0]:
display(new_ml_df)

start_lat start_lng end_lat end_lng ride_duration(sec) hour_of_day day_of_week day_of_month month year distance(miles) average_speed(mps) bearing Holiday ride_availability start_station_index is_member is_casual is_electric_bike is_classic_bike is_docked_bike 37.77460716666667 -122.41390233333334 37.794525 -122.3948805 940 16 5 25 5 2023 1.7241837449918407 0.0018342380265870646 37.03849863932578 0 0 413.0 1 0 1 0 0 37.774578 -122.41389766666667 37.772354 -122.4358575 560 16 5 25 5 2023 1.2091210082749795 0.0021591446576338918 262.70542261632556 0 0 413.0 1 0 1 0 0 37.7744791 -122.4139142 37.79416044174933 -122.42156758904456 878 16 5 25 5 2023 1.422622175277843 0.001620298605100049 342.91863273633925 0 0 413.0 1 0 0 1 0 37.774491 -122.41393133333334 37.7737172 -122.4116467 125 16 5 25 5 2023 0.13574440128047038 0.0010859552102437631 113.19428539648197 0 0 413.0 1 0 1 0 0 37.774572666666664 -122.41385083333333 37.7813455 -122.418409 339 18 5 25 5 2023 0.5300458532922455 0.0015635570893576564 331.9911527946609 0 1 413.0 1 0 1 0 0 37.7744791 -122.4139142 37.7737172 -122.4116467 76 1 6 26 5 2023 0.1345610501864768 0.0017705401340325894 113.02941539504775 0 0 413.0 1 0 0 1 0 37.7744791 -122.4139142 37.7737172 -122.4116467 112 8 7 27 5 2023 0.1345610501864768 0.0012014379480935428 113.02941539504775 1 0 413.0 1 0 0 1 0 37.7745695 -122.41393966666666 37.7840775 -122.411926 366 7 2 29 5 2023 0.6660803045696055 0.001819891542539906 9.5020829721268 1 0 413.0 1 0 1 0 0 37.77450433333333 -122.41389166666667 37.7785885 -122.392553 443 13 2 29 5 2023 1.1990233665184136 0.0027065990214862608 76.38126385629164 1 0 413.0 0 1 1 0 0 37.774510666666664 -122.41390883333334 37.78383 -122.39887 466 9 3 30 5 2023 1.043597767355894 0.002239480187459 51.897671885138095 0 0 413.0 1 0 1 0 0 37.77454016666667 -122.41387 37.764783 -122.3908972 577 6 4 31 5 2023 1.424348206948903 0.0024685410865665563 118.24223316413247 0 0 413.0 1 0 1 0 0 37.774538 -122.41389516666666 37.776619 -122.417385 149 9 7 3 6 2023 0.23874197098668568 0.0016022951072931925 307.03259829857416 1 0 413.0 1 0 1 0 0 37.774577 -122.41388583333334 37.7645435 -122.410349 3672 19 1 4 6 2023 0.7196589880103959 1.95985563183659E-4 164.4286170930077 1 1 413.0 1 0 1 0 0 37.774551 -122.41387033333334 37.764285 -122.4318042 602 12 4 7 6 2023 1.2093540623699994 0.0020088937913122916 234.09489077762237 0 1 413.0 1 0 1 0 0 37.77457616666667 -122.41380866666667 37.7662185 -122.4310597 505 12 4 7 6 2023 1.1050701372000733 0.0021882576974258878 238.50150050571932 0 1 413.0 0 1 1 0 0 37.774505258 -122.41387856 37.785479 -122.419342 400 17 5 8 6 2023 0.8148024144578543 0.0020370060361446355 338.5221890645006 0 1 413.0 1 0 1 0 0 37.774553166666664 -122.4138825 37.769263 -122.407054 280 17 5 8 6 2023 0.5221936820941495 0.0018649774360505339 134.42185948719077 0 1 413.0 1 0 1 0 0 37.774537333333335 -122.41394233333334 37.78383 -122.39887 404 9 6 9 6 2023 1.0439036986965773 0.0025839200462786567 52.03919332413551 0 0 413.0 1 0 1 0 0 37.7744791 -122.4139142 37.7735069 -122.4160402 56 18 7 10 6 2023 0.13413952220543568 0.0023953486108113514 239.94990550565203 1 0 413.0 1 0 0 1 0 37.77453333333333 -122.41388433333333 37.79416044174933 -122.42156758904456 501 0 1 11 6 2023 1.419521900771309 0.002833377047447722 342.81129335537514 1 0 413.0 1 0 1 0 0 37.774540186 -122.413870215 37.77599270441184 -122.39300568626935 417 11 3 13 6 2023 1.1438811412410996 0.0027431202427844114 84.96024009222174 0 0 413.0 1 0 1 0 0 37.77453383333334 -122.4138635 37.7645435 -122.410349 269 11 3 13 6 2023 0.7164586078324316 0.0026634148990053222 164.45856413975264 0 0 413.0 1 0 1 0 0 37.774523497 -122.413877606 37.7892792 -122.4450687 1008 17 3 13 6 2023 1.9850911163106757 0.0019693364249113846 300.9127762634595 0 0 413.0 1 0 1 0 0 37.7744791 -122.4139142 37.7737172 -122.4116467 84 17 3 13 6 2023 0.1345610501864768 0.0016019172641247238 113.02941539504775 0 0 413.0 1 0 0 1 0 37.7744791 -122.4139142 37.765429 -122.42189 447 0 4 14 6 202

In [0]:
# Counting Rows in "new_ml_df".
new_ml_df.count()

4649938

In [0]:
# List of columns excluding "ride_availability"
input_cols = [col for col in new_ml_df.columns if col != "ride_availability"]

# Create a vector assembler
vector_assembler = VectorAssembler(
    inputCols=input_cols,
    outputCol="features"
)

# Create a standard scaler
scaler = StandardScaler(inputCol="features", outputCol="scaled_features", withStd=True, withMean=True)

# Initialize the logistic regression model
logistic_reg = LogisticRegression(featuresCol="features", labelCol="ride_availability", maxIter=100, tol=1e-5)

# Create a pipeline
pipeline = Pipeline(stages=[vector_assembler, scaler, logistic_reg])

# Split your data into training and testing sets
(train_data, test_data) = new_ml_df.randomSplit([0.8, 0.2], seed=123)

# Cache the training data to avoid redundant computations
train_data.cache()

# Fit the pipeline to the training data
model = pipeline.fit(train_data)

# Make predictions on the test data
predictions = model.transform(test_data)

# Evaluate the model (e.g., using BinaryClassificationEvaluator)
evaluator = BinaryClassificationEvaluator(labelCol="ride_availability")
accuracy = evaluator.evaluate(predictions, {evaluator.metricName: "areaUnderROC"})
print(f"Area under ROC curve: {accuracy}")

# Evaluate the model
evaluator = MulticlassClassificationEvaluator(labelCol="ride_availability", metricName="accuracy")
accuracy = evaluator.evaluate(predictions)
print(f"Accuracy: {accuracy}")

Uploading artifacts:   0%|          | 0/4 [00:00<?, ?it/s]

Area under ROC curve: 0.6446257024710756
Accuracy: 0.8435248610832126


In [0]:
# List of columns excluding "ride_availability"
input_cols = [col for col in new_ml_df.columns if col != "ride_availability"]

# Create a vector assembler
vector_assembler = VectorAssembler(inputCols=input_cols, outputCol="features")

# Initialize the Multilayer Perceptron model
layers = [len(input_cols), 15, 10, 5, 2] 
mlp = MultilayerPerceptronClassifier(featuresCol="features", labelCol="ride_availability", layers=layers, seed=123)

# Create a pipeline
pipeline = Pipeline(stages=[vector_assembler, mlp])

# Split your data into training and testing sets
(train_data, test_data) = new_ml_df.randomSplit([0.8, 0.2], seed=123)

# Fit the pipeline to the training data
model = pipeline.fit(train_data)

# Make predictions on the test data
predictions = model.transform(test_data)

# Evaluate the model
evaluator = BinaryClassificationEvaluator(labelCol="ride_availability", metricName="areaUnderROC")
accuracy = evaluator.evaluate(predictions)
print(f"Area under ROC curve for Multilayer Perceptron Classifier: {accuracy}")

# Evaluate the model
evaluator = MulticlassClassificationEvaluator(labelCol="ride_availability", metricName="accuracy")
accuracy = evaluator.evaluate(predictions)
print(f"Accuracy for Multilayer Perceptron Classifier: {accuracy}")

Area under ROC curve for Multilayer Perceptron Classifier: 0.627605148446402
Accuracy for Multilayer Perceptron Classifier: 0.8435248610832126


In [0]:
# List of columns excluding "ride_availability"
input_cols = [col for col in new_ml_df.columns if col != "ride_availability"]

# Create a vector assembler
vector_assembler = VectorAssembler(
    inputCols=input_cols,
    outputCol="features"
)

# Initialize the Random Forest model
random_forest = RandomForestClassifier(featuresCol="features", labelCol="ride_availability", maxDepth=10, numTrees=100, maxBins=600)

# Create a pipeline
pipeline = Pipeline(stages=[vector_assembler, random_forest])

# Split your data into training and testing sets
(train_data, test_data) = new_ml_df.randomSplit([0.8, 0.2], seed=123)

# Cache the training data to avoid redundant computations
train_data.cache()

# Fit the pipeline to the training data
model = pipeline.fit(train_data)

# Make predictions on the test data
predictions = model.transform(test_data)

# Evaluate the model (e.g., using BinaryClassificationEvaluator)
evaluator = BinaryClassificationEvaluator(labelCol="ride_availability", metricName="areaUnderROC")
accuracy = evaluator.evaluate(predictions)
print(f"Area under ROC curve: {accuracy}")

# Evaluate the model
evaluator = MulticlassClassificationEvaluator(labelCol="ride_availability", metricName="accuracy")
accuracy = evaluator.evaluate(predictions)
print(f"Accuracy: {accuracy}")

**Model Performance Evaluation**

The ROC (Receiver Operating Characteristic) curve is a metric used to evaluate the performance of classification models. Accuracy represents the proportion of correctly classified instances out of the total instances. Below are the ROC curve scores and Accuracy scores for different machine learning models:

- **Logistic Regression:**
  - ROC: 0.644
  - Accuracy: 0.843

- **Random Forest:**
  - ROC: 0.688
  - Accuracy: 0.782

- **Multilayer Perceptron Classifier:**
  - ROC: 0.627
  - Accuracy: 0.843

A higher ROC score and higher Accuracy indicate better model performance in distinguishing between classes. The Logistic Regression Classifier demonstrates the highest ROC and Accuracy scores among the evaluated models, suggesting superior discriminatory power.


In [0]:
# The following line is used to stop the Spark Session, which is essential to release resources and gracefully shut down the Spark application. 
# It is good practice to include this line at the end of your Spark application to avoid resource leaks and to ensure proper cleanup.
# Once the Spark Session is stopped, any further Spark operations will not be possible in the current application.
# This is especially important when running Spark applications in interactive environments or scripts to prevent unnecessary resource usage.

spark.stop()